In [61]:
from bs4 import  BeautifulSoup
import pandas as pd
import requests
import json
import csv

In [62]:
# Extracting the url html data

base_url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
index = requests.get(base_url).text
soup = BeautifulSoup(index, 'html.parser')

In [63]:
%pprint
soup

Pretty printing has been turned ON



<!DOCTYPE html>

<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of postal codes of Canada: M - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgMonthNamesShort":["","Jan","Feb","Mar","Apr","May","Jun","Jul","Aug","Sep","Oct","Nov","Dec"],"wgRequestId":"XnJb2QpAEKAAA8f2JaUAAACU","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","wgTitle":"List of postal codes of Canada: M","wgCurRevisionId":946188405,"wgRevisionId":946188405,"wgArticleId":539066,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles with short des

In [64]:
# Store all tags of (td,p) in list l
l=[]   

for tags in soup.find_all('td' and 'p'):
    l.append(tags)

In [65]:
# extracting only tags which has information of table content

info=l[3:]
info

[<p><b>M1A</b><br/><span style="font-size:80%;"><i>Not assigned</i></span>
 </p>,
 <p><b>M2A</b><br/><span style="font-size:80%;"><i>Not assigned</i></span>
 </p>,
 <p><b>M3A</b><br/><span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>)</span>
 </p>,
 <p><b>M4A</b><br/><span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>)</span>
 </p>,
 <p><b>M5A</b><br/><span style="font-size:80%;"><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a><br/>(<a href="/wiki/Regent_Park" title="Regent Park">Regent Park</a> / <a class="mw-redirect" href="/wiki/Harbourfront,_Toronto" title="Harbourfront, Toronto">Harbourfront</a>)</span>
 </p>,
 <p><b>M6A</b><br/><span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="

In [66]:
#Just checking that all tags are extracted with all information table content

for i,tag in enumerate(info):
    print(i,tag)
    

0 <p><b>M1A</b><br/><span style="font-size:80%;"><i>Not assigned</i></span>
</p>
1 <p><b>M2A</b><br/><span style="font-size:80%;"><i>Not assigned</i></span>
</p>
2 <p><b>M3A</b><br/><span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>)</span>
</p>
3 <p><b>M4A</b><br/><span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>)</span>
</p>
4 <p><b>M5A</b><br/><span style="font-size:80%;"><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a><br/>(<a href="/wiki/Regent_Park" title="Regent Park">Regent Park</a> / <a class="mw-redirect" href="/wiki/Harbourfront,_Toronto" title="Harbourfront, Toronto">Harbourfront</a>)</span>
</p>
5 <p><b>M6A</b><br/><span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wik

In [67]:
#Just checking that in span tag city and neighbourhood city is present

for i,tag in enumerate(info):
    for a in tag.find_all('span'):
         print(i,a)

0 <span style="font-size:80%;"><i>Not assigned</i></span>
1 <span style="font-size:80%;"><i>Not assigned</i></span>
2 <span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>)</span>
3 <span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>)</span>
4 <span style="font-size:80%;"><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a><br/>(<a href="/wiki/Regent_Park" title="Regent Park">Regent Park</a> / <a class="mw-redirect" href="/wiki/Harbourfront,_Toronto" title="Harbourfront, Toronto">Harbourfront</a>)</span>
5 <span style="font-size:80%;"><a href="/wiki/North_York" title="North York">North York</a><br/>(<a href="/wiki/Lawrence_Manor" title="Lawrence Manor">Lawrence Manor</a> / <a href="/wiki/Lawrence_Heights" title="Lawrence Heights">Lawrence Heig

In [68]:
#Extracting table in outer_lst

outer_lst = []     # here we storing rows which are in list format
nn_lst = []        # here we store list after breaking a row against '('

for i,tag in enumerate(info):
    for a in tag.find_all('span'):
        inside_lst = []                                 # In this list we store pincode,city,neighbour and reuse it again
        if(a.text == 'Not assigned'):
            None                                        # Don't consider the rows which has NO VALUES
        else:
            name_neig = a.text
            if('(' in name_neig):                       # if ( present then split rows into list
                nn_lst = name_neig.split('(')       
                if(')' in nn_lst[-1]):
                    #print(nn_lst[-1])
                    loc = nn_lst[-1].find(')')         # remove the ')' character from the end of the last element of list
                    #print(loc)
                    nn_lst[-1] = nn_lst[-1][:loc]
            elif('/' in name_neig):                    # if '(' is not present the split against '/'
                nn_lst = name_neig.split('/')
            #print(tag.find('b').text)
            #print(nn_lst[0])
            #print(nn_lst[1:])
            nn_lst[-1] = nn_lst[-1].replace('/',',')    
            inside_lst.append(tag.find('b').text)      # store postalcode,city ,neighbourhood in list
            inside_lst.append(nn_lst[0])
            inside_lst.append(nn_lst[1:])        
            #print(inside_lst)
            outer_lst.append(inside_lst)            # store list of row in outer_lst

outer_lst

[['M3A', 'North York', ['Parkwoods']],
 ['M4A', 'North York', ['Victoria Village']],
 ['M5A', 'Downtown Toronto', ['Regent Park , Harbourfront']],
 ['M6A', 'North York', ['Lawrence Manor , Lawrence Heights']],
 ['M7A', "Queen's Park ", [' Ontario Provincial Government']],
 ['M9A', 'Etobicoke', ['Islington Avenue']],
 ['M1B', 'Scarborough', ['Malvern , Rouge']],
 ['M3B', 'North York', ['Don Mills']],
 ['M4B', 'East York', ['Parkview Hill , Woodbine Gardens']],
 ['M5B', 'Downtown Toronto', ['Garden District, Ryerson']],
 ['M6B', 'North York', ['Glencairn']],
 ['M9B',
  'Etobicoke',
  ['West Deane Park , Princess Gardens , Martin Grove , Islington , Cloverdale']],
 ['M1C', 'Scarborough', ['Rouge Hill , Port Union , Highland Creek']],
 ['M3C', 'North York', ['Don Mills)South', 'Flemingdon Park']],
 ['M4C', 'East York', ['Woodbine Heights']],
 ['M5C', 'Downtown Toronto', ['St. James Town']],
 ['M6C', 'York', ['Humewood-Cedarvale']],
 ['M9C',
  'Etobicoke',
  ['Eringate , Bloordale Gardens ,

In [69]:
#Create data frame with proper columns name

df = pd.DataFrame(columns =['Postalcode','Borough','Neighbourhood'], data=outer_lst)
df

Postalcode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A                                      Queen's Park    
5          M9A                                          Etobicoke   
6          M1B                                        Scarborough   
7          M3B                                         North York   
8          M4B                                          East York   
9          M5B                                   Downtown Toronto   
10         M6B                                         North York   
11         M9B                                          Etobicoke   
12         M1C                                        Scarborough   
13         M3C                                         North York   
14         M4C                                          East York   
15         M5C                                   Downtown Toronto   
16         M6C                                               York   
17         M9C                                          Etobicoke   
18         M1E                                        Scarborough   
19         M4E                                       East Toronto   
20         M5E                                   Downtown Toronto   
21         M6E                                               York   
22         M1G                                        Scarborough   
23         M4G                                          East York   
24         M5G                                   Downtown Toronto   
25         M6G                                   Downtown Toronto   
26         M1H                                        Scarborough   
27         M2H                                         North York   
28         M3H                                         North York   
29         M4H                                          East York   
30         M5H                                   Downtown Toronto   
31         M6H                                       West Toronto   
32         M1J                                        Scarborough   
33         M2J                                         North York   
34         M3J                                         North York   
35         M4J                              East YorkEast Toronto   
36         M5J                                   Downtown Toronto   
37         M6J                                       West Toronto   
38         M1K                                        Scarborough   
39         M2K                                         North York   
40         M3K                                         North York   
41         M4K                                       East Toronto   
42         M5K                                   Downtown Toronto   
43         M6K                                       West Toronto   
44         M1L                                        Scarborough   
45         M2L                                         North York   
46         M3L                                         North York   
47         M4L                                       East Toronto   
48         M5L                                   Downtown Toronto   
49         M6L                                         North York   
50         M9L                                         North York   
51         M1M                                        Scarborough   
52         M2M                                         North York   
53         M3M                                         North York   
54         M4M                                       East Toronto   
55         M5M                                         North York   
56         M6M                                               York   
57

In [70]:
#change llist of neighbourhood int strings

df['Neighbourhood'] = [''.join(map(str, l)) for l in df['Neighbourhood']]
df

Postalcode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A                                      Queen's Park    
5          M9A                                          Etobicoke   
6          M1B                                        Scarborough   
7          M3B                                         North York   
8          M4B                                          East York   
9          M5B                                   Downtown Toronto   
10         M6B                                         North York   
11         M9B                                          Etobicoke   
12         M1C                                        Scarborough   
13         M3C                                         North York   
14         M4C                                          East York   
15         M5C                                   Downtown Toronto   
16         M6C                                               York   
17         M9C                                          Etobicoke   
18         M1E                                        Scarborough   
19         M4E                                       East Toronto   
20         M5E                                   Downtown Toronto   
21         M6E                                               York   
22         M1G                                        Scarborough   
23         M4G                                          East York   
24         M5G                                   Downtown Toronto   
25         M6G                                   Downtown Toronto   
26         M1H                                        Scarborough   
27         M2H                                         North York   
28         M3H                                         North York   
29         M4H                                          East York   
30         M5H                                   Downtown Toronto   
31         M6H                                       West Toronto   
32         M1J                                        Scarborough   
33         M2J                                         North York   
34         M3J                                         North York   
35         M4J                              East YorkEast Toronto   
36         M5J                                   Downtown Toronto   
37         M6J                                       West Toronto   
38         M1K                                        Scarborough   
39         M2K                                         North York   
40         M3K                                         North York   
41         M4K                                       East Toronto   
42         M5K                                   Downtown Toronto   
43         M6K                                       West Toronto   
44         M1L                                        Scarborough   
45         M2L                                         North York   
46         M3L                                         North York   
47         M4L                                       East Toronto   
48         M5L                                   Downtown Toronto   
49         M6L                                         North York   
50         M9L                                         North York   
51         M1M                                        Scarborough   
52         M2M                                         North York   
53         M3M                                         North York   
54         M4M                                       East Toronto   
55         M5M                                         North York   
56         M6M                                               York   
57

In [71]:
# Change the number of character can be printed at once

pd.get_option('display.max_rows')
pd.set_option('display.max_rows',1000)
pd.set_option('display.max_columns',1000)

In [72]:
df

Postalcode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A                                      Queen's Park    
5          M9A                                          Etobicoke   
6          M1B                                        Scarborough   
7          M3B                                         North York   
8          M4B                                          East York   
9          M5B                                   Downtown Toronto   
10         M6B                                         North York   
11         M9B                                          Etobicoke   
12         M1C                                        Scarborough   
13         M3C                                         North York   
14         M4C                                          East York   
15         M5C                                   Downtown Toronto   
16         M6C                                               York   
17         M9C                                          Etobicoke   
18         M1E                                        Scarborough   
19         M4E                                       East Toronto   
20         M5E                                   Downtown Toronto   
21         M6E                                               York   
22         M1G                                        Scarborough   
23         M4G                                          East York   
24         M5G                                   Downtown Toronto   
25         M6G                                   Downtown Toronto   
26         M1H                                        Scarborough   
27         M2H                                         North York   
28         M3H                                         North York   
29         M4H                                          East York   
30         M5H                                   Downtown Toronto   
31         M6H                                       West Toronto   
32         M1J                                        Scarborough   
33         M2J                                         North York   
34         M3J                                         North York   
35         M4J                              East YorkEast Toronto   
36         M5J                                   Downtown Toronto   
37         M6J                                       West Toronto   
38         M1K                                        Scarborough   
39         M2K                                         North York   
40         M3K                                         North York   
41         M4K                                       East Toronto   
42         M5K                                   Downtown Toronto   
43         M6K                                       West Toronto   
44         M1L                                        Scarborough   
45         M2L                                         North York   
46         M3L                                         North York   
47         M4L                                       East Toronto   
48         M5L                                   Downtown Toronto   
49         M6L                                         North York   
50         M9L                                         North York   
51         M1M                                        Scarborough   
52         M2M                                         North York   
53         M3M                                         North York   
54         M4M                                       East Toronto   
55         M5M                                         North York   
56         M6M                                               York   
57

In [73]:
#Save table into CSV file format

df.to_csv('postalCode_city_neghbourhood10.csv')

In [74]:
#Shape
df.shape

(103, 3)

# Assignment 2 - Segmenting and Clustering Neighborhoods in Toronto

In [75]:
#Read other file with latitude and longitude data
#!wget -q -O 'Toronto_long_lat_data.csv'  http://cocl.us/Geospatial_data
  
df_lon_lat = pd.read_csv('Geospatial_Coordinates.csv')
df_lon_lat.columns=['Postalcode','Latitude','Longitude']
df_lon_lat.head()

Postalcode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [76]:
#Matchng two dataframe using column  Postal Code

Toronto_df = pd.merge(df,
                      df_lon_lat,
                      on='Postalcode')
Toronto_df

Postalcode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A                                      Queen's Park    
5          M9A                                          Etobicoke   
6          M1B                                        Scarborough   
7          M3B                                         North York   
8          M4B                                          East York   
9          M5B                                   Downtown Toronto   
10         M6B                                         North York   
11         M9B                                          Etobicoke   
12         M1C                                        Scarborough   
13         M3C                                         North York   
14         M4C                                          East York   
15         M5C                                   Downtown Toronto   
16         M6C                                               York   
17         M9C                                          Etobicoke   
18         M1E                                        Scarborough   
19         M4E                                       East Toronto   
20         M5E                                   Downtown Toronto   
21         M6E                                               York   
22         M1G                                        Scarborough   
23         M4G                                          East York   
24         M5G                                   Downtown Toronto   
25         M6G                                   Downtown Toronto   
26         M1H                                        Scarborough   
27         M2H                                         North York   
28         M3H                                         North York   
29         M4H                                          East York   
30         M5H                                   Downtown Toronto   
31         M6H                                       West Toronto   
32         M1J                                        Scarborough   
33         M2J                                         North York   
34         M3J                                         North York   
35         M4J                              East YorkEast Toronto   
36         M5J                                   Downtown Toronto   
37         M6J                                       West Toronto   
38         M1K                                        Scarborough   
39         M2K                                         North York   
40         M3K                                         North York   
41         M4K                                       East Toronto   
42         M5K                                   Downtown Toronto   
43         M6K                                       West Toronto   
44         M1L                                        Scarborough   
45         M2L                                         North York   
46         M3L                                         North York   
47         M4L                                       East Toronto   
48         M5L                                   Downtown Toronto   
49         M6L                                         North York   
50         M9L                                         North York   
51         M1M                                        Scarborough   
52         M2M                                         North York   
53         M3M                                         North York   
54         M4M                                       East Toronto   
55         M5M                                         North York   
56         M6M                                               York   
57

In [77]:
Toronto_df[Toronto_df['Borough']=='Downtown Toronto']
Toronto_df.to_csv('file10.csv')

# Explore and cluster the neighborhoods in Toronto

In [78]:
import random # library for random number generation

#!conda install -c conda-forge geopy --yes 

from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images

from IPython.display import Image 
from IPython.core.display import HTML 

# tranforming json file into a pandas dataframe library

from pandas.io.json import json_normalize

#!conda install -c conda-forge folium=0.5.0 --yes

import folium # plotting library

print('Folium installed')
print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Folium installed
Libraries imported.


# Define Foursquare Credentials and Version

In [79]:
CLIENT_ID = '02SEA0J343IKQHUWUC0OFSPRPZHCOEWWVPKDISU2IHFTRDH1' # your Foursquare ID\n",
CLIENT_SECRET = 'ET5JNM2NC04JAUE005HMGACJB3ABJQT3H1HXMY55BBETKDDH' # your Foursquare Secret\n",
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 02SEA0J343IKQHUWUC0OFSPRPZHCOEWWVPKDISU2IHFTRDH1
CLIENT_SECRET:ET5JNM2NC04JAUE005HMGACJB3ABJQT3H1HXMY55BBETKDDH


In [80]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="Toronto")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print(latitude, longitude)

43.653963 -79.387207


In [81]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map

for lat, lng, borough, Neighbourhood in zip(Toronto_df['Latitude'], Toronto_df['Longitude'], Toronto_df['Borough'], Toronto_df['Neighbourhood']):
    label = '{}, {}'.format(Neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)

    folium.CircleMarker([lat, lng],
                        radius=5,
                        popup=label,
                        color='red',
                        fill=True,
                        fill_color='#3186cc',
                        fill_opacity=0.7,
                        parse_html=False).add_to(map_toronto)
    
map_toronto

### Let's explore the first neighborhood in our dataframe.

In [82]:
Toronto_df.loc[0,'Neighbourhood']

'Parkwoods'

In [83]:
neighborhood_latitude = Toronto_df.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = Toronto_df.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = Toronto_df.loc[0,'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude,
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


##### get the top 100 venues that are in Marble Hill within a radius of 500 meters

In [84]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

#Create API Request URL

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    VERSION,
    neighborhood_latitude,
    neighborhood_longitude,
    radius,
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=02SEA0J343IKQHUWUC0OFSPRPZHCOEWWVPKDISU2IHFTRDH1&client_secret=ET5JNM2NC04JAUE005HMGACJB3ABJQT3H1HXMY55BBETKDDH&v=20180604&ll=43.7532586,-79.3296565&radius=500&limit=100'

In [85]:
#get information in json format

results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e77a13a216785001b56c118'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 2,
  'suggestedBounds': {'ne': {'lat': 43.757758604500005,
    'lng': -79.32343823984928},
   'sw': {'lat': 43.7487585955, 'lng': -79.33587476015072}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs': 

In [86]:
venues = results['response']['groups'][0]['items']
venues

[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
   'name': 'Brookbanks Park',
   'location': {'address': 'Toronto',
    'lat': 43.751976046055574,
    'lng': -79.33214044722958,
    'labeledLatLngs': [{'label': 'display',
      'lat': 43.751976046055574,
      'lng': -79.33214044722958}],
    'distance': 245,
    'cc': 'CA',
    'city': 'Toronto',
    'state': 'ON',
    'country': 'Canada',
    'formattedAddress': ['Toronto', 'Toronto ON', 'Canada']},
   'categories': [{'id': '4bf58dd8d48988d163941735',
     'name': 'Park',
     'pluralName': 'Parks',
     'shortName': 'Park',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/park_',
      'suffix': '.png'},
     'primary': True}],
   'photos': {'count': 0, 'groups': []}},
  'referralId': 'e-0-4e8d9dcdd5fbbbb6b3003c7b-0'},
 {'reasons': {'count': 0,
   'items': [{'

In [87]:
nearby_venues = json_normalize(venues) # flatten JSON
nearby_venues

C:\Users\BLACK\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """Entry point for launching an IPython kernel.


referralId  reasons.count  \
0  e-0-4e8d9dcdd5fbbbb6b3003c7b-0              0   
1  e-0-4cb11e2075ebb60cd1c4caad-1              0   

                                       reasons.items  \
0  [{'summary': 'This spot is popular', 'type': '...   
1  [{'summary': 'This spot is popular', 'type': '...   

                   venue.id       venue.name venue.location.address  \
0  4e8d9dcdd5fbbbb6b3003c7b  Brookbanks Park                Toronto   
1  4cb11e2075ebb60cd1c4caad    Variety Store   29 Valley Woods Road   

   venue.location.lat  venue.location.lng  \
0           43.751976          -79.332140   
1           43.751974          -79.333114   

                       venue.location.labeledLatLngs  venue.location.distance  \
0  [{'label': 'display', 'lat': 43.75197604605557...                      245   
1  [{'label': 'display', 'lat': 43.75197441585782...                      312   

  venue.location.cc venue.location.city venue.location.state  \
0                CA             Toronto                   ON   
1                CA             Toronto                   ON   

  venue.location.country             venue.location.formattedAddress  \
0                 Canada               [Toronto, Toronto ON, Canada]   
1                 Canada  [29 Valley Woods Road, Toronto ON, Canada]   

                                    venue.categories  venue.photos.count  \
0  [{'id': '4bf58dd8d48988d163941735', 'name': 'P...                   0   
1  [{'id': '4bf58dd8d48988d1f9941735', 'name': 'F...                   0   

  venue.photos.groups  
0                  []  
1                  []

In [88]:
#filter columns

filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]
nearby_venues

venue.name                                   venue.categories  \
0  Brookbanks Park  [{'id': '4bf58dd8d48988d163941735', 'name': 'P...   
1    Variety Store  [{'id': '4bf58dd8d48988d1f9941735', 'name': 'F...   

   venue.location.lat  venue.location.lng  
0           43.751976          -79.332140  
1           43.751974          -79.333114

In [89]:
#function that extracts the category of the venue

def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [90]:
# filter the category for each row

nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)
['venue.categories']

['venue.categories']

In [91]:
nearby_venues

venue.name   venue.categories  venue.location.lat  venue.location.lng
0  Brookbanks Park               Park           43.751976          -79.332140
1    Variety Store  Food & Drink Shop           43.751974          -79.333114

In [92]:
# clean columns

nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]
nearby_venues.columns

Index(['name', 'categories', 'lat', 'lng'], dtype='object')

In [93]:
nearby_venues.head()

name         categories        lat        lng
0  Brookbanks Park               Park  43.751976 -79.332140
1    Variety Store  Food & Drink Shop  43.751974 -79.333114

# Number of venues returend

In [94]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

2 venues were returned by Foursquare.


# We learned how to Explore 1 neighbourhood

## Now Explore all Neighborhoods in Toronto

In [95]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [96]:
toronto_venues = getNearbyVenues(names=Toronto_df['Neighbourhood'],
                                   latitudes=Toronto_df['Latitude'],
                                   longitudes=Toronto_df['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park , Harbourfront
Lawrence Manor , Lawrence Heights
 Ontario Provincial Government
Islington Avenue
Malvern , Rouge
Don Mills
Parkview Hill , Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park , Princess Gardens , Martin Grove , Islington , Cloverdale
Rouge Hill , Port Union , Highland Creek
Don Mills)SouthFlemingdon Park
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate , Bloordale Gardens , Old Burnhamthorpe , Markland Wood
Guildwood , Morningside , West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor , Wilson Heights , Downsview North
Thorncliffe Park
Richmond , Adelaide , King
Dufferin , Dovercourt Village
Scarborough Village
Fairview , Henry Farm , Oriole
Northwood Park , York University
The Danforth  East
Harbourfront East , Union Station , Toronto Islands
Little Portugal , Trinity
Kennedy Park , Ionview , East Birchmount Park
Bayvi

In [97]:
toronto_venues.head(10)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                   Parkwoods              43.753259              -79.329656   
1                   Parkwoods              43.753259              -79.329656   
2            Victoria Village              43.725882              -79.315572   
3            Victoria Village              43.725882              -79.315572   
4            Victoria Village              43.725882              -79.315572   
5            Victoria Village              43.725882              -79.315572   
6  Regent Park , Harbourfront              43.654260              -79.360636   
7  Regent Park , Harbourfront              43.654260              -79.360636   
8  Regent Park , Harbourfront              43.654260              -79.360636   
9  Regent Park , Harbourfront              43.654260              -79.360636   

                                       Venue  Venue Latitude  Venue Longitude  \
0                            Brookbanks Park       43.751976       -79.332140   
1                              Variety Store       43.751974       -79.333114   
2                     Victoria Village Arena       43.723481       -79.315635   
3                                Tim Hortons       43.725517       -79.313103   
4                                  Portugril       43.725819       -79.312785   
5  Eglinton Ave E & Sloane Ave/Bermondsey Rd       43.726086       -79.313620   
6                           Roselle Desserts       43.653447       -79.362017   
7                              Tandem Coffee       43.653559       -79.361809   
8                     Cooper Koo Family YMCA       43.653249       -79.358008   
9                        Body Blitz Spa East       43.654735       -79.359874   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant  
5           Intersection  
6                 Bakery  
7            Coffee Shop  
8    Distribution Center  
9                    Spa

In [98]:
toronto_venues.shape

(2247, 7)

#### Let's check how many venues were returned for each neighborhood

In [99]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
 Ontario Provincial Government                                         41   
Agincourt                                                               5   
Alderwood , Long Branch                                                 9   
Bathurst Manor , Wilson Heights , Downsview North                      21   
Bayview Village                                                         4   
Bedford Park , Lawrence Manor East                                     26   
Berczy Park                                                            56   
Birch Cliff , Cliffside West                                            4   
Brockton , Parkdale Village , Exhibition Place                         24   
CN Tower , King and Spadina , Railway Lands , H...                     16   
Caledonia-Fairbanks                                                     4   
Cedarbrae                                                               9   
Central Bay Street                                                     83   
Christie                                                               18   
Church and Wellesley                                                   87   
Clairville , Humberwood , Woodbine Downs , West...                      2   
Clarks Corners , Tam O'Shanter , Sullivan                              14   
Cliffside , Cliffcrest , Scarborough Village West                       2   
Commerce Court , Victoria Hotel                                       100   
Davisville                                                             38   
Davisville North                                                        7   
Del Ray , Mount Dennis , Keelsdale and Silverthorn                      4   
Don Mills                                                               5   
Don Mills)SouthFlemingdon Park                                         21   
Dorset Park , Wexford Heights , Scarborough Tow...                      7   
Downsview                                                              12   
Downsview)East  CFB Toronto                                             2   
Dufferin , Dovercourt Village                                          19   
Enclave of L4W                                                         13   
Enclave of M4L                                                         18   
Enclave of M5E                                                         95   
Eringate , Bloordale Gardens , Old Burnhamthorp...                      9   
Fairview , Henry Farm , Oriole                                         65   
First Canadian Place , Underground city                               100   
Forest Hill North & West                                                5   
Garden District, Ryerson                                              100   
Glencairn                                                               5   
Golden Mile , Clairlea , Oakridge                                      10   
Guildwood , Morningside , West Hill                                     8   
Harbourfront East , Union Station , Toronto Isl...                    100   
High Park , The Junction South                                         24   
Hillcrest Village                                                       4   
Humber Summit                                                           2   
Humberlea , Emery                                                       2   
Humewood-Cedarvale                                                      4   
India Bazaar , The Beaches West                                        20   
Kennedy Park , Ionview , East Birchmount Park                           5   
Kensington Market , Chinatown , Grange Park                            87   
Kingsview Village , St. Phillips , Martin Grove...                      4   
Lawrence Manor , Lawrence Heights                                      14   
Lawrence Park                                   

#### How many unique venue category are here

In [100]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 274 uniques categories.


## Lets Analyse each Neighbourhood

In [101]:
# one hot encoding

toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")
toronto_onehot

Accessories Store  Afghan Restaurant  Airport  Airport Food Court  \
0                     0                  0        0                   0   
1                     0                  0        0                   0   
2                     0                  0        0                   0   
3                     0                  0        0                   0   
4                     0                  0        0                   0   
...                 ...                ...      ...                 ...   
2242                  0                  0        0                   0   
2243                  0                  0        0                   0   
2244                  0                  0        0                   0   
2245                  0                  0        0                   0   
2246                  0                  0        0                   0   

      Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0                0               0                0                 0   
1                0               0                0                 0   
2                0               0                0                 0   
3                0               0                0                 0   
4                0               0                0                 0   
...            ...             ...              ...               ...   
2242             0               0                0                 0   
2243             0               0                0                 0   
2244             0               0                0                 0   
2245             0               0                0                 0   
2246             0               0                0                 0   

      American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                       0             0         0            0           0   
1                       0             0         0            0           0   
2                       0             0         0            0           0   
3                       0             0         0            0           0   
4                       0             0         0            0           0   
...                   ...           ...       ...          ...         ...   
2242                    0             0         0            0           0   
2243                    0             0         0            0           0   
2244                    0             0         0            0           0   
2245                    0             0         0            0           0   
2246                    0             0         0            0           0   

      Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                       0                 0                   0            0   
1                       0                 0                   0            0   
2                       0                 0                   0            0   
3                       0                 0                   0            0   
4                       0                 0                   0            0   
...                   ...               ...                 ...          ...   
2242                    0                 0                   0            0   
2243                    0                 0                   0            0   
2244                    0                 0                   0            0   
2245                    0                 0                   0            0   
2246                    0                 0                   0            0   

      Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                 0          0           0           0       0     0    0   
1                 0          0           0           0       0     0    0   
2                 0          0           0           0       0     0    0   
3                 0   

In [102]:
# add neighborhood column back to dataframe

toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood']
toronto_onehot['Neighborhood']

0                                               Parkwoods
1                                               Parkwoods
2                                        Victoria Village
3                                        Victoria Village
4                                        Victoria Village
                              ...                        
2242    Mimico NW , The Queensway West , South of Bloo...
2243    Mimico NW , The Queensway West , South of Bloo...
2244    Mimico NW , The Queensway West , South of Bloo...
2245    Mimico NW , The Queensway West , South of Bloo...
2246    Mimico NW , The Queensway West , South of Bloo...
Name: Neighborhood, Length: 2247, dtype: object

In [103]:
# move neighborhood column to the first column

fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]
toronto_onehot

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0               0                  0                  0        0   
1               0                  0                  0        0   
2               0                  0                  0        0   
3               0                  0                  0        0   
4               0                  0                  0        0   
...           ...                ...                ...      ...   
2242            0                  0                  0        0   
2243            0                  0                  0        0   
2244            0                  0                  0        0   
2245            0                  0                  0        0   
2246            0                  0                  0        0   

      Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                      0             0               0                0   
1                      0             0               0                0   
2                      0             0               0                0   
3                      0             0               0                0   
4                      0             0               0                0   
...                  ...           ...             ...              ...   
2242                   0             0               0                0   
2243                   0             0               0                0   
2244                   0             0               0                0   
2245                   0             0               0                0   
2246                   0             0               0                0   

      Airport Terminal  American Restaurant  Antique Shop  Aquarium  \
0                    0                    0             0         0   
1                    0                    0             0         0   
2                    0                    0             0         0   
3                    0                    0             0         0   
4                    0                    0             0         0   
...                ...                  ...           ...       ...   
2242                 0                    0             0         0   
2243                 0                    0             0         0   
2244                 0                    0             0         0   
2245                 0                    0             0         0   
2246                 0                    0             0         0   

      Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0               0           0                    0                 0   
1               0           0                    0                 0   
2               0           0                    0                 0   
3               0           0                    0                 0   
4               0           0                    0                 0   
...           ...         ...                  ...               ...   
2242            0           0                    0                 0   
2243            0           0                    0                 0   
2244            0           0                    0                 0   
2245            0           0                    0                 0   
2246            0           0                    0                 0   

      Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0                      0            0              0          0           0   
1                      0            0              0          0           0   
2                      0            0              0          0           0   
3                      0            0              0          0           0   
4                      0            0              0          0           0   
...                  ...          ...            ...        ...         ...   
2242             

In [104]:
# Examine the new data frame

toronto_onehot.shape

(2247, 274)

In [105]:
#let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                       Ontario Provincial Government     0.024390   
1                                           Agincourt     0.000000   
2                             Alderwood , Long Branch     0.000000   
3   Bathurst Manor , Wilson Heights , Downsview North     0.000000   
4                                     Bayview Village     0.000000   
5                  Bedford Park , Lawrence Manor East     0.000000   
6                                         Berczy Park     0.000000   
7                        Birch Cliff , Cliffside West     0.000000   
8      Brockton , Parkdale Village , Exhibition Place     0.000000   
9   CN Tower , King and Spadina , Railway Lands , ...     0.000000   
10                                Caledonia-Fairbanks     0.000000   
11                                          Cedarbrae     0.000000   
12                                 Central Bay Street     0.012048   
13                                           Christie     0.000000   
14                               Church and Wellesley     0.011494   
15  Clairville , Humberwood , Woodbine Downs , Wes...     0.000000   
16          Clarks Corners , Tam O'Shanter , Sullivan     0.000000   
17  Cliffside , Cliffcrest , Scarborough Village West     0.000000   
18                    Commerce Court , Victoria Hotel     0.000000   
19                                         Davisville     0.000000   
20                                   Davisville North     0.000000   
21  Del Ray , Mount Dennis , Keelsdale and Silvert...     0.000000   
22                                          Don Mills     0.000000   
23                     Don Mills)SouthFlemingdon Park     0.000000   
24  Dorset Park , Wexford Heights , Scarborough To...     0.000000   
25                                          Downsview     0.000000   
26                        Downsview)East  CFB Toronto     0.000000   
27                      Dufferin , Dovercourt Village     0.000000   
28                                     Enclave of L4W     0.000000   
29                                     Enclave of M4L     0.000000   
30                                     Enclave of M5E     0.000000   
31  Eringate , Bloordale Gardens , Old Burnhamthor...     0.000000   
32                     Fairview , Henry Farm , Oriole     0.000000   
33            First Canadian Place , Underground city     0.000000   
34                           Forest Hill North & West     0.000000   
35                           Garden District, Ryerson     0.000000   
36                                          Glencairn     0.000000   
37                  Golden Mile , Clairlea , Oakridge     0.000000   
38                Guildwood , Morningside , West Hill     0.000000   
39  Harbourfront East , Union Station , Toronto Is...     0.000000   
40                     High Park , The Junction South     0.000000   
41                                  Hillcrest Village     0.000000   
42                                      Humber Summit     0.000000   
43                                  Humberlea , Emery     0.000000   
44                                 Humewood-Cedarvale     0.000000   
45                    India Bazaar , The Beaches West     0.000000   
46      Kennedy Park , Ionview , East Birchmount Park     0.000000   
47        Kensington Market , Chinatown , Grange Park     0.000000   
48  Kingsview Village , St. Phillips , Martin Grov...     0.000000   
49                  Lawrence Manor , Lawrence Heights     0.000000   
50                                      Lawrence Park     0.000000   
51                                            Leaside     0.000000   
52                          Little Portugal , Trinity     0.018182   
53                                    Malvern , Rouge     0.000000   
54  Milliken , Agincourt North , Steeles East , L'...     0.000000   
55  Mimico NW , The Queensway West , South of Bloo...     0.000000   
56                       Moore Park , Summerhill Ea

In [106]:
# confirm the new size

toronto_grouped.shape

(96, 274)

## Let's print each neighborhood along with the top 5 most common venues

In [109]:
for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    #temp = toronto_grouped[toronto_grouped['Neighborhood']
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    print(temp)

---- Ontario Provincial Government----
                               index                               0
0                       Neighborhood   Ontario Provincial Government
1                        Yoga Studio                       0.0243902
2                  Accessories Store                               0
3                  Afghan Restaurant                               0
4                            Airport                               0
5                 Airport Food Court                               0
6                       Airport Gate                               0
7                     Airport Lounge                               0
8                    Airport Service                               0
9                   Airport Terminal                               0
10               American Restaurant                               0
11                      Antique Shop                               0
12                          Aquarium                            

In [57]:
for hood in toronto_grouped['Neighborhood']:
    #print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]                                # all rows axcept 0th
    print(temp)

                               venue       freq
1                        Yoga Studio  0.0243902
2                  Accessories Store          0
3                  Afghan Restaurant          0
4                            Airport          0
5                 Airport Food Court          0
6                       Airport Gate          0
7                     Airport Lounge          0
8                    Airport Service          0
9                   Airport Terminal          0
10               American Restaurant          0
11                      Antique Shop          0
12                          Aquarium          0
13                       Art Gallery          0
14                        Art Museum          0
15               Arts & Crafts Store  0.0243902
16                  Asian Restaurant          0
17                Athletics & Sports          0
18                       Auto Garage          0
19                     Auto Workshop          0
20                         BBQ Joint    

In [110]:
# sort in descending order of freq of venues
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    #print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

          venue  freq
0   Coffee Shop  0.22
1          Park  0.05
2   Yoga Studio  0.02
3    Hobby Shop  0.02
4  Burger Joint  0.02


                       venue  freq
0                     Lounge   0.2
1             Breakfast Spot   0.2
2               Skating Rink   0.2
3             Clothing Store   0.2
4  Latin American Restaurant   0.2


         venue  freq
0  Pizza Place  0.22
1          Gym  0.11
2  Coffee Shop  0.11
3         Pool  0.11
4          Pub  0.11


                 venue  freq
0                 Bank  0.10
1          Coffee Shop  0.10
2             Pharmacy  0.05
3     Sushi Restaurant  0.05
4  Fried Chicken Joint  0.05


                 venue  freq
0                 Café  0.25
1                 Bank  0.25
2  Japanese Restaurant  0.25
3   Chinese Restaurant  0.25
4          Yoga Studio  0.00


                  venue  freq
0    Italian Restaurant  0.08
1           Coffee Shop  0.08
2        Sandwich Place  0.08
3            Restaurant  0.08
4  Fast Food Restaurant 

In [112]:
# Function to sort the venues in descending order.

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [114]:
#create the new dataframe and display the top 10 venues for each neighborhood.
import numpy as np

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                      Ontario Provincial Government           Coffee Shop   
1                                          Agincourt                Lounge   
2                            Alderwood , Long Branch           Pizza Place   
3  Bathurst Manor , Wilson Heights , Downsview North           Coffee Shop   
4                                    Bayview Village   Japanese Restaurant   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                       Park                   Gym        Discount Store   
1  Latin American Restaurant          Skating Rink        Clothing Store   
2               Skating Rink           Coffee Shop              Pharmacy   
3                       Bank             Pet Store        Sandwich Place   
4         Chinese Restaurant                  Café                  Bank   

  5th Most Common Venue      6th Most Common Venue 7th Most Common Venue  \
0            Restaurant      Portuguese Restaurant             Nightclub   
1        Breakfast Spot                 Donut Shop                 Diner   
2                  Pool                        Pub        Sandwich Place   
3           Supermarket  Middle Eastern Restaurant         Shopping Mall   
4                 Diner             Discount Store   Distribution Center   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0    Mexican Restaurant             Juice Bar     Italian Restaurant  
1        Discount Store   Distribution Center                Dog Run  
2                   Gym       Airport Service   Ethiopian Restaurant  
3            Restaurant         Deli / Bodega                  Diner  
4               Dog Run      Doner Restaurant          Women's Store

# Cluster Neighborhoods

## Run k-means to cluster the neighborhood into 5 clusters

In [117]:
# set number of clusters
from sklearn.cluster import KMeans

kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 4, 0, 0, 0, 0, 0, 0, 0])

#### Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood. 

In [121]:
# add clustering labels
#neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = Toronto_df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbourhood')

toronto_merged.head() # check the last columns!

Postalcode           Borough                      Neighbourhood   Latitude  \
0        M3A        North York                          Parkwoods  43.753259   
1        M4A        North York                   Victoria Village  43.725882   
2        M5A  Downtown Toronto         Regent Park , Harbourfront  43.654260   
3        M6A        North York  Lawrence Manor , Lawrence Heights  43.718518   
4        M7A     Queen's Park       Ontario Provincial Government  43.662301   

   Longitude  Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
0 -79.329656             1.0                  Park       Food & Drink Shop   
1 -79.315572             0.0           Coffee Shop            Intersection   
2 -79.360636             0.0           Coffee Shop                    Park   
3 -79.464763             0.0        Clothing Store  Furniture / Home Store   
4 -79.389494             0.0           Coffee Shop                    Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0          Women's Store      Doner Restaurant    Dim Sum Restaurant   
1  Portuguese Restaurant          Hockey Arena         Women's Store   
2                    Pub                Bakery    Mexican Restaurant   
3          Women's Store           Coffee Shop    Miscellaneous Shop   
4                    Gym        Discount Store            Restaurant   

   6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0                  Diner        Discount Store    Distribution Center   
1                Dog Run    Dim Sum Restaurant                  Diner   
2                   Café               Theater  Performing Arts Venue   
3             Shoe Store              Boutique            Event Space   
4  Portuguese Restaurant             Nightclub     Mexican Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0               Dog Run             Donut Shop  
1        Discount Store    Distribution Center  
2                   Spa             Shoe Store  
3             Gift Shop  Vietnamese Restaurant  
4             Juice Bar     Italian Restaurant

In [123]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        fill=True,
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examine Clusters
#### Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster.

###### Cluster 1

In [124]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels  \
1                                           North York             0.0   
2                                     Downtown Toronto             0.0   
3                                           North York             0.0   
4                                        Queen's Park              0.0   
7                                           North York             0.0   
8                                            East York             0.0   
9                                     Downtown Toronto             0.0   
12                                         Scarborough             0.0   
13                                          North York             0.0   
14                                           East York             0.0   
15                                    Downtown Toronto             0.0   
16                                                York             0.0   
17                                           Etobicoke             0.0   
18                                         Scarborough             0.0   
19                                        East Toronto             0.0   
20                                    Downtown Toronto             0.0   
22                                         Scarborough             0.0   
23                                           East York             0.0   
24                                    Downtown Toronto             0.0   
25                                    Downtown Toronto             0.0   
26                                         Scarborough             0.0   
27                                          North York             0.0   
28                                          North York             0.0   
29                                           East York             0.0   
30                                    Downtown Toronto             0.0   
31                                        West Toronto             0.0   
32                                         Scarborough             0.0   
33                                          North York             0.0   
34                                          North York             0.0   
36                                    Downtown Toronto             0.0   
37                                        West Toronto             0.0   
38                                         Scarborough             0.0   
39                                          North York             0.0   
41                                        East Toronto             0.0   
42                                    Downtown Toronto             0.0   
43                                        West Toronto             0.0   
44                                         Scarborough             0.0   
45                                          North York             0.0   
46                                          North York             0.0   
47                                        East Toronto             0.0   
48                                    Downtown Toronto             0.0   
51                                         Scarborough             0.0   
53                                          North York             0.0   
54                                        East Toronto             0.0   
55                                          North York             0.0   
56                                                York             0.0   
57                                          North York             0.0   
58                                         Scarborough             0.0   
59                                          North York             0.0   
60                                          North York             0.0   
65                                         Scarborough             0.0   
67                                     Central Toronto             0.0   
68                                     Central Toronto             0.0   
69                                        West Toro

###### Cluster 2 

In [125]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0              North York             1.0                  Park   
21                   York             1.0                  Park   
35  East YorkEast Toronto             1.0     Convenience Store   
40             North York             1.0               Airport   
49             North York             1.0                  Park   
61        Central Toronto             1.0              Bus Line   
64                   York             1.0     Convenience Store   
66             North York             1.0     Convenience Store   
83        Central Toronto             1.0          Tennis Court   
85            Scarborough             1.0            Playground   
91       Downtown Toronto             1.0                  Park   
98              Etobicoke             1.0                 River   

   2nd Most Common Venue       3rd Most Common Venue 4th Most Common Venue  \
0      Food & Drink Shop               Women's Store      Doner Restaurant   
21         Women's Store                      Market      Doner Restaurant   
35           Coffee Shop                        Park         Women's Store   
40                  Park               Women's Store            Donut Shop   
49                Bakery  Construction & Landscaping         Women's Store   
61                  Park                 Swim School         Women's Store   
64                  Park                  Donut Shop    Dim Sum Restaurant   
66                  Park                        Bank            Donut Shop   
83                  Park                  Playground            Restaurant   
85                  Park               Women's Store               Dog Run   
91            Playground                       Trail         Women's Store   
98                  Park               Women's Store   Distribution Center   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0     Dim Sum Restaurant                 Diner        Discount Store   
21    Dim Sum Restaurant                 Diner        Discount Store   
35    Dim Sum Restaurant                 Diner        Discount Store   
40    Dim Sum Restaurant                 Diner        Discount Store   
49            Donut Shop                 Diner        Discount Store   
61               Dog Run    Dim Sum Restaurant                 Diner   
64                 Diner        Discount Store   Distribution Center   
66                 Diner        Discount Store   Distribution Center   
83        Discount Store         Deli / Bodega      Department Store   
85      Department Store          Dessert Shop    Dim Sum Restaurant   
91   Distribution Center      Department Store          Dessert Shop   
98      Department Store          Dessert Shop    Dim Sum Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0    Distribution Center               Dog Run             Donut Shop  
21   Distribution Center               Dog Run              Drugstore  
35   Distribution Center               Dog Run       Doner Restaurant  
40   Distribution Center               Dog Run       Doner Restaurant  
49   Distribution Center               Dog Run       Doner Restaurant  
61        Discount Store   Distribution Center       Doner Restaurant  
64               Dog Run      Doner Restaurant          Women's Store  
66               Dog Run      Doner Restaurant          Women's Store  
83          Dessert Shop    Dim Sum Restaurant                  Diner  
85                 Diner        Discount Store    Distribution Center  
91    Dim Sum Restaurant                 Diner         Discount Store  
98                 Diner        Discount Store                Dog Run

##### Cluster 3 

In [126]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
6  Scarborough             2.0  Fast Food Restaurant         Women's Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6                 Diner        Discount Store   Distribution Center   

  9th Most Common Venue 10th Most Common Venue  
6               Dog Run             Donut Shop

###### Cluster 4 

In [127]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
62  Central Toronto             3.0                Garden   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
62         Women's Store               Dog Run          Dessert Shop   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
62    Dim Sum Restaurant                 Diner        Discount Store   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
62   Distribution Center      Doner Restaurant          Deli / Bodega

##### Cluster 5 

In [128]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
10  North York             4.0           Pizza Place                  Park   
50  North York             4.0   Empanada Restaurant           Pizza Place   
63        York             4.0           Pizza Place     Convenience Store   
70   Etobicoke             4.0           Pizza Place        Discount Store   
77   Etobicoke             4.0           Pizza Place     Mobile Phone Shop   
93   Etobicoke             4.0           Pizza Place          Skating Rink   

   3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
10                   Pub   Japanese Restaurant  Eastern European Restaurant   
50         Women's Store               Dog Run                 Dessert Shop   
63         Grocery Store              Bus Line           Dim Sum Restaurant   
70        Sandwich Place          Intersection           Chinese Restaurant   
77              Bus Line        Sandwich Place          Distribution Center   
93           Coffee Shop              Pharmacy                         Pool   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
10   Dumpling Restaurant             Drugstore            Donut Shop   
50    Dim Sum Restaurant                 Diner        Discount Store   
63                 Diner        Discount Store   Distribution Center   
70           Coffee Shop   Dumpling Restaurant             Drugstore   
77    Dim Sum Restaurant                 Diner        Discount Store   
93                   Pub        Sandwich Place                   Gym   

   9th Most Common Venue 10th Most Common Venue  
10      Doner Restaurant          Deli / Bodega  
50   Distribution Center             Donut Shop  
63               Dog Run       Doner Restaurant  
70            Donut Shop       Doner Restaurant  
77               Dog Run       Department Store  
93       Airport Service   Ethiopian Restaurant